## CogVideoX Text-to-Video
## CogVideoX Text-to-Video+Audio

#### Install the necessary requirements

In [ ]:
!pip install diffusers transformers hf_transfer

In [ ]:
# !pip install git+https://github.com/huggingface/accelerate
!pip install accelerate==0.33.0

  Using cached numpy-1.26.4-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (61 kB)
Using cached numpy-1.26.4-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (18.3 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 2.2.6
    Uninstalling numpy-2.2.6:
      Successfully uninstalled numpy-2.2.6
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
thinc 8.3.6 requires numpy<3.0.0,>=2.0.0, but you have numpy 1.26.4 which is incompatible.


In [ ]:
!pip install numpy==1.24.4 --force-reinstall
!pip install diffusers --force-reinstall


  Using cached numpy-1.24.4-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (5.6 kB)
Using cached numpy-1.24.4-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (17.3 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 1.26.4
    Uninstalling numpy-1.26.4:
      Successfully uninstalled numpy-1.26.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.18.0 requires numpy<2.1.0,>=1.26.0, but you have numpy 1.24.4 which is incompatible.
thinc 8.3.6 requires numpy<3.0.0,>=2.0.0, but you have numpy 1.24.4 which is incompatible.
treescope 0.1.9 requires numpy>=1.25.2, but you have numpy 1.24.4 which is incompatible.
jax 0.5.2 requires numpy>=1.25, but you have numpy 1.24.4 which is incompatible.
pymc 5.22.0 requires numpy>=1.25.0, but you have numpy 1.24.4 which is incompatible.
blosc2 3.3.3 requires numpy>=1

  Using cached diffusers-0.33.1-py3-none-any.whl.metadata (19 kB)
  Using cached importlib_metadata-8.7.0-py3-none-any.whl.metadata (4.8 kB)
  Using cached filelock-3.18.0-py3-none-any.whl.metadata (2.9 kB)
  Using cached huggingface_hub-0.32.2-py3-none-any.whl.metadata (14 kB)
  Using cached numpy-2.2.6-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (62 kB)
  Using cached regex-2024.11.6-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (40 kB)
  Using cached requests-2.32.3-py3-none-any.whl.metadata (4.6 kB)
  Using cached safetensors-0.5.3-cp38-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (3.8 kB)
  Using cached pillow-11.2.1-cp311-cp311-manylinux_2_28_x86_64.whl.metadata (8.9 kB)
  Using cached fsspec-2025.5.1-py3-none-any.whl.metadata (11 kB)
  Using cached packaging-25.0-py3-none-any.whl.metadata (3.3 kB)
  Using cached PyYAML-6.0.2-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (2.1 kB)
  Using cached tq

In [ ]:
!pip install git+https://github.com/huggingface/diffusers.git --upgrade --quiet
!pip install transformers --quiet


  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


#### Import required libraries

The following block is optional but if enabled, downloading models from the HF Hub will be much faster

In [ ]:
# Environment settings
import os
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"
os.environ["HF_HUB_ENABLE_HF_TRANSFER"] = "1"


In [ ]:
# Imports
import torch
import gc
from diffusers import AutoencoderKLCogVideoX, CogVideoXPipeline, CogVideoXTransformer3DModel
from diffusers import CogVideoXPipeline, AutoencoderKLCogVideoX, CogVideoXTransformer3DModel
from diffusers.utils import export_to_video
from transformers import T5EncoderModel

# Use official THUDM repo (not camenduru)
model_id = "THUDM/CogVideoX-2b"

#### ⚙️ Model Loading & Precision Note

We use `float16` for running **CogVideoX-2b**, since `bfloat16` is not well supported on Colab’s Turing GPUs and can cause out-of-memory (OOM) errors.

While `float16` may slightly reduce video quality, it's necessary on low-end GPUs. For best performance and quality, use **Ampere or newer GPUs**, which support optimized kernels (like those from [TorchAO](https://github.com/pytorch/ao)).


In [ ]:

# Load model in float16 directly from THUDM (will auto-convert layers that support it)
transformer = CogVideoXTransformer3DModel.from_pretrained(
    model_id,
    subfolder="transformer",
    torch_dtype=torch.float16
)

text_encoder = T5EncoderModel.from_pretrained(
    model_id,
    subfolder="text_encoder",
    torch_dtype=torch.float16
)

vae = AutoencoderKLCogVideoX.from_pretrained(
    model_id,
    subfolder="vae",
    torch_dtype=torch.float16
)


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/758 [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/3.39G [00:00<?, ?B/s]

config.json:   0%|          | 0.00/783 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/19.9k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/4.53G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

config.json:   0%|          | 0.00/879 [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/862M [00:00<?, ?B/s]

In [ ]:
# Create pipeline and run inference
pipe = CogVideoXPipeline.from_pretrained(
    model_id,
    text_encoder=text_encoder,
    transformer=transformer,
    vae=vae,
    torch_dtype=torch.float16,
)


model_index.json:   0%|          | 0.00/411 [00:00<?, ?B/s]

scheduler_config.json:   0%|          | 0.00/482 [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/2.59k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.54k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/20.6k [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/5 [00:00<?, ?it/s]

#### 🧠 Memory Optimization (for Colab/Low VRAM)

To run this model on Colab or older GPUs (like Turing), we use **sequential CPU offloading**. This keeps most of the model on the CPU and moves only the active part to the GPU.

It saves VRAM but makes generation much slower (can take 1+ hour). For now, it's the only way to run CogVideoX on limited hardware until faster kernels are available.


In [ ]:
# Offload to CPU and tile VAE
pipe.enable_sequential_cpu_offload()
pipe.vae.enable_tiling()

#### Generate!

In [ ]:
prompt = (
    "A brown dog runs energetically after a gray cat on a grassy path." "The camera follows them from behind with a smooth cinematic motion."
"The cat is ahead, looking back fearfully, while the dog is determined."
"The sun is setting, casting long shadows on the ground."
)

In [ ]:
# Clear GPU memory
torch.cuda.empty_cache()
gc.collect()

# Run generation (use fewer steps if needed)
video_output = pipe(
    prompt=prompt,
    guidance_scale=6,
    use_dynamic_cfg=True,
    num_inference_steps=25  # Try 15–25 for Colab
).frames[0]

# Export to video
export_to_video(video_output, output_video_path="panda_music.mp4")


  0%|          | 0/25 [00:00<?, ?it/s]

'panda_music.mp4'

## CogVideoX Text-to-Video+Audio

This project demonstrates how natural language prompts can be transformed into realistic videos using the **CogVideoX** model. CogVideoX is a state-of-the-art generative model built on top of transformer-based architecture, designed for high-quality text-to-video synthesis.

The system uses three key components:
- **Text Encoder (T5)**: Converts the input prompt into machine-understandable embeddings.
- **Transformer3D**: Learns the temporal and spatial structure of the video.
- **VAE (Variational Autoencoder)**: Reconstructs high-quality frames from compressed latent representations.

In addition, we use **gTTS (Google Text-to-Speech)** to create spoken narration from the prompt, and **MoviePy** to merge the video and audio, producing a synchronized, narrated video.

The output is a short cinematic clip that reflects the described scene — generated purely from text, showcasing the power of multimodal AI.



In [ ]:
# STEP 1: Environment Settings
import os
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"
os.environ["HF_HUB_ENABLE_HF_TRANSFER"] = "1"

# STEP 2: Install Required Libraries
!pip install -q diffusers transformers accelerate moviepy gtts

# STEP 3: Imports
import torch, gc
from diffusers import AutoencoderKLCogVideoX, CogVideoXPipeline, CogVideoXTransformer3DModel
from transformers import T5EncoderModel
from diffusers.utils import export_to_video
from gtts import gTTS
from moviepy.editor import VideoFileClip, AudioFileClip

# STEP 4: Load CogVideoX Model
model_id = "THUDM/CogVideoX-2b"

transformer = CogVideoXTransformer3DModel.from_pretrained(
    model_id, subfolder="transformer", torch_dtype=torch.float16
)

text_encoder = T5EncoderModel.from_pretrained(
    model_id, subfolder="text_encoder", torch_dtype=torch.float16
)

vae = AutoencoderKLCogVideoX.from_pretrained(
    model_id, subfolder="vae", torch_dtype=torch.float16
)

pipe = CogVideoXPipeline.from_pretrained(
    model_id,
    text_encoder=text_encoder,
    transformer=transformer,
    vae=vae,
    torch_dtype=torch.float16
)

pipe.enable_sequential_cpu_offload()
pipe.vae.enable_tiling()

# STEP 5: Prompt
prompt = (
    "A brown dog runs energetically after a gray cat on a grassy path. "
    "The camera follows them from behind with a smooth cinematic motion. "
    "The cat is ahead, looking back fearfully, while the dog is determined. "
    "The sun is setting, casting long shadows on the ground."
)

# STEP 6: Clear GPU memory
torch.cuda.empty_cache()
gc.collect()

# STEP 7: Generate Video from Prompt
video_frames = pipe(
    prompt=prompt,
    guidance_scale=6,
    use_dynamic_cfg=True,
    num_inference_steps=25
).frames[0]

video_path = "dog_chasing_cat.mp4"
export_to_video(video_frames, output_video_path=video_path)

# STEP 8: Generate Narration using gTTS
tts = gTTS(prompt)
tts.save("narration.mp3")

# STEP 9: Combine Video + Audio
video_clip = VideoFileClip(video_path)
audio_clip = AudioFileClip("narration.mp3").set_duration(video_clip.duration)
final_clip = video_clip.set_audio(audio_clip)
final_clip.write_videofile("final_output.mp4", codec='libx264', audio_codec='aac')

# STEP 10: Display Video in Colab
from IPython.display import Video
Video("final_output.mp4", embed=True)


The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(



Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Loading pipeline components...:   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/25 [00:00<?, ?it/s]

Moviepy - Building video final_output.mp4.
MoviePy - Writing audio in final_outputTEMP_MPY_wvf_snd.mp4


MoviePy - Done.
Moviepy - Writing video final_output.mp4



Moviepy - Done !
Moviepy - video ready final_output.mp4
